# Topic Modelling Notebook 

In [ ]:
# Utilities
from joblib import Parallel, delayed
from pandarallel import pandarallel
pandarallel.initialize(progress_bar=True)
from multiprocessing import Pool, cpu_count
import warnings 
warnings.filterwarnings("ignore")
import os
import pandas as pd
import numpy as np
import tqdm
from tqdm import tqdm
tqdm.pandas(desc="progress bar")
import gc
os.environ['TOKENIZERS_PARALLELISM'] = 'true'

# Import time packages 
import time
import datetime

# Visualization Tools
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px

# Deep Learning Models 
import torch
import tensorflow as tf

# Topic Modelling Packages
from transformers import AutoTokenizer, AutoModelForSequenceClassification
#from bertopic import BERTopic


In [4]:
from utils import search_folder
current_dir = os.getcwd()
thesis_folder_path = current_dir.replace("/laptop code/thesis_code", "")
twitter_data_path = search_folder(thesis_folder_path,"twitter_data")
eikon_data_path = search_folder(thesis_folder_path,"eikon_news")
topic_modelling = search_folder(thesis_folder_path, "topic_modelling")

In [5]:
# Retrieving sentiment on cleaned text
twitter_df = pd.read_csv(twitter_data_path +"/twitter_senti_df.csv")
twitter_df["datetime"] = pd.to_datetime(twitter_df["datetime"])
twitter_df =twitter_df.sort_values(by = "datetime")
twitter_df = twitter_df.drop_duplicates()

In [6]:
# Retrieving Sentiment on Eikon Raw News 
eikon_df = pd.read_csv(eikon_data_path +"/raw_eikon_senti_df.csv")
eikon_df["datetime"] = pd.to_datetime(eikon_df["datetime"])
eikon_df = eikon_df.sort_values(by = "datetime")

In [7]:
print(twitter_df.shape)
print(eikon_df.shape)

(2157988, 21)
(44423, 16)


In [8]:
# Tweets on Saturday and Sunday are moved to Monday in order to not losse any relevance
from utils import fix_dates
twitter_df["datetime"] = twitter_df["datetime"].progress_apply(lambda x: fix_dates(x))
eikon_df["datetime"] = eikon_df["datetime"].progress_apply(lambda x: fix_dates(x))

progress bar: 100%|██████████| 44423/44423 [00:00<00:00, 468987.48it/s]


---
## Finbert-tone-finetuned-finance-topic-classification
This model is a fine-tuned version of yiyanghkust/finbert-tone on Twitter Financial News Topic dataset.
Model determines the financial topic of given tweets over 20 various topics. Given the unbalanced distribution of the class labels, the weights were adjusted to pay attention to the less sampled labels which should increase overall performance.

In [9]:
# Instantiating the model 
tokenizer = AutoTokenizer.from_pretrained("nickmuchi/finbert-tone-finetuned-finance-topic-classification")
model = AutoModelForSequenceClassification.from_pretrained("nickmuchi/finbert-tone-finetuned-finance-topic-classification")

In [37]:
def topic_classifier(tweet: str):
    with tf.device('/device:GPU:0'):
        tokens = tokenizer.encode_plus(tweet, truncation=True, padding=True, return_tensors="pt", max_length= 512)
        outputs = model(**tokens)
        class_probs = outputs.logits.softmax(dim=1)
        output_class = class_probs.argmax().item()
        topic = topics_list[output_class]
        return topic

---
### Quick Test on Publicly Available Dataset 

In [11]:
tweets_train = pd.read_csv(thesis_folder_path+ "/topic_modelling/train_data.csv")
tweets_valid = pd.read_csv(thesis_folder_path+ "/topic_modelling/valid_data.csv")

In [12]:
topics = {
        "LABEL_0": "Analyst Update",
        "LABEL_1": "Fed & Central Banks",
        "LABEL_2": "Company & Product News",
        "LABEL_3": "Treasuries & Corporate Debt",
        "LABEL_4": "Dividend",
        "LABEL_5": "Earnings",
        "LABEL_6": "Energy & Oil",
        "LABEL_7": "Financials",
        "LABEL_8": "Currencies",
        "LABEL_9": "General News & Opinion",
        "LABEL_10": "Gold, Metals & Materials",
        "LABEL_11": "IPO",
        "LABEL_12": "Legal & Regulation",
        "LABEL_13": "M&A & Investments",
        "LABEL_14": "Macro",
        "LABEL_15": "Markets",
        "LABEL_16": "Politics",
        "LABEL_17": "Personnel Change",
        "LABEL_18": "Stock Commentary",
        "LABEL_19": "Stock Movement",
    }

topics_list = list(topics.values())

In [25]:
#tweets_valid["pred"] = tweets_valid["text"].progress_apply(lambda tweet: topic_classifier(tweet))

In [26]:
#accuracy_score(tweets_valid["label"].values,tweets_valid["pred"].values)*100

----
### Classifying Tweets into different Topics 

In [22]:
eikon_subset = eikon_df[["datetime", "company", "text", "cleaned_text"]]
twitter_subset = twitter_df[["datetime", "company", "text", "cleaned_text"]]

In [24]:
companies = list(twitter_subset["company"].unique())[:-1]
companies.sort(reverse=True)
companies = ["moderna","apple", "tesla", "google"]

In [25]:
companies

['moderna', 'apple', 'tesla', 'google']

In [26]:
twitter_subset["company"].value_counts()

tesla      1250193
apple       674679
google      184195
moderna      48780
Name: company, dtype: int64

In [27]:
def handle_topic_classifier(tweet):
    try:
        topic = topic_classifier(tweet)
        return topic
    except Exception as e:
        print(f"Error occurred for tweet: {tweet}")
        print(f"Error message: {str(e)}")
        return None


In [95]:
tesla_subset = twitter_df.copy()
tesla_subset = tesla_subset[tesla_subset["company"] == "apple"]
tesla_subset = tesla_subset[["datetime", "company", "text", "cleaned_text", "Vader_sentim"]]

In [96]:
with tf.device('/device:GPU:0'):
    tesla_subset["topic"] = tesla_subset["text"].progress_apply(lambda tweet: handle_topic_classifier(tweet))

progress bar: 100%|██████████| 674679/674679 [32:11:45<00:00,  5.82it/s]     


In [97]:
tesla_subset

datetime company  \
0       2017-01-02 00:04:53+00:00   apple   
2       2017-01-02 00:14:25+00:00   apple   
3       2017-01-02 00:38:06+00:00   apple   
10      2017-01-02 01:10:47+00:00   apple   
15      2017-01-02 01:13:19+00:00   apple   
...                           ...     ...   
2167949 2023-04-14 21:22:38+00:00   apple   
2167951 2023-04-14 21:28:23+00:00   apple   
2167952 2023-04-14 21:30:08+00:00   apple   
2167968 2023-04-14 22:32:33+00:00   apple   
2167974 2023-04-14 22:50:03+00:00   apple   

                                                      text  \
0        Review: Bragi's Headphone offers a solid alter...   
2        Roasted Persian Chicken and Cauliflower | Mark...   
3        Apple also integrated DTrace into macOS and wr...   
10       adage: ICYMI: How Apple alienated Mac loyalist...   
15       $AAPL OI for maturity 01/06/2017. 104.00 Highe...   
...                                                    ...   
2167949  Monopoly GO Takes the Classic Board Game in a ...   
2167951  $VIX $SPY $DIA $QQQ $NDX $NVDA $META $CMG $AZO...   
2167952  $TSLA $AAPL $NVDA i wuz worried about our shor...   
2167968  HomeKit Weekly: Matter support comes to smart ...   
2167974  Spotify is shutting down its 'Heardle' song gu...   

                                              cleaned_text  Vader_sentim  \
0        review 's headphone offers a solid alternative...        0.1531   
2        roasted persian chicken and cauliflower | mark...        0.0000   
3        apple also integrated into macos and wrote som...        0.4215   
10                 adage how apple alienated mac loyalists        0.2732   
15       apple oi for maturity 104.00 highest put 119.0...        0.0000   
...                                                    ...           ...   
2167949  monopoly go takes the classic board game in a ...        0.5106   
2167951                    spy dia meta azo ulta elf apple        0.0000   
2167952  tesla apple i wuz worried about our shorts but...        0.5023   
2167968  weekly matter support comes to smart plugs wit...        0.6705   
2167974  spotify is shutting down its song guessing gam...        0.1027   

                          topic  
0        Company & Product News  
2        Company & Product News  
3        Company & Product News  
10       Company & Product News  
15             Stock Commentary  
...                         ...  
2167949        Stock Commentary  
2167951        Stock Commentary  
2167952        Stock Commentary  
2167968        Stock Commentary  
2167974  Company & Product News  

[674679 rows x 6 columns]

In [98]:
tesla_subset["date"] = tesla_subset["datetime"].dt.strftime('%Y-%m-%d')
tesla_subset_grouped = pd.DataFrame(tesla_subset.groupby(by = ["date", "topic"])["Vader_sentim"].sum())
tesla_subset_grouped["date"] = pd.to_datetime(tesla_subset_grouped["date"])
tesla_subset_grouped = tesla_subset_grouped.reset_index()

In [89]:
tesla_subset_grouped.head(7)

date                   topic  Vader_sentim
0  2017-01-03  Company & Product News        0.0000
1  2017-01-03          Stock Movement        0.5994
2  2017-01-04  Company & Product News        0.8481
3  2017-01-04        Stock Commentary        2.1985
4  2017-01-05        Stock Commentary        0.4215
5  2017-01-09  Company & Product News        2.3788
6  2017-01-09        Stock Commentary        0.5267

In [168]:
moderna_topics = pd.read_csv(topic_modelling+ "/moderna_topic_senti.csv")
apple_topics = pd.read_csv(topic_modelling+ "/apple_topic_senti.csv")
tesla_topics = pd.read_csv(topic_modelling+ "/tesla_topic_senti.csv")

In [112]:
moderna_topics.groupby(["topic"])["topic"].count().sort_values(ascending = False)

topic
Stock Commentary               1129
Company & Product News         1034
General News & Opinion          811
Stock Movement                  810
Macro                           416
Legal & Regulation              386
Politics                        292
Markets                         287
Analyst Update                  283
Earnings                        211
M&A & Investments               187
Financials                      103
Personnel Change                 94
Treasuries & Corporate Debt      74
IPO                              52
Energy & Oil                     45
Fed & Central Banks              30
Gold, Metals & Materials         29
Currencies                       23
Dividend                          1
Name: topic, dtype: int64

In [118]:
apple_topics.groupby(["topic"])["topic"].count().sort_values(ascending = False)

topic
Stock Commentary               1640
Company & Product News         1640
Stock Movement                 1634
General News & Opinion         1620
Markets                        1563
Legal & Regulation             1548
Analyst Update                 1523
M&A & Investments              1400
Earnings                       1238
Macro                          1092
Politics                       1008
Financials                      977
Treasuries & Corporate Debt     682
Fed & Central Banks             675
Personnel Change                589
Energy & Oil                    440
Dividend                        402
IPO                             298
Currencies                      181
Gold, Metals & Materials        167
Name: topic, dtype: int64

In [169]:
tesla_topics

date                        topic  Vader_sentim
0      2017-01-02               Analyst Update        2.6299
1      2017-01-02       Company & Product News        5.0529
2      2017-01-02       General News & Opinion       -0.0941
3      2017-01-02           Legal & Regulation       -2.3734
4      2017-01-02                      Markets        0.5106
...           ...                          ...           ...
23199  2023-04-14                      Markets        0.4576
23200  2023-04-14                     Politics        0.0273
23201  2023-04-14             Stock Commentary       23.7870
23202  2023-04-14               Stock Movement       -0.2660
23203  2023-04-14  Treasuries & Corporate Debt       -0.0128

[23204 rows x 3 columns]

In [167]:
tesla_topics_count = pd.DataFrame(tesla_topics.groupby(["date","topic"])["topic"].count())
tesla_topics_count

topic
date       topic                             
2017-01-02 Analyst Update                   1
           Company & Product News           1
           General News & Opinion           1
           Legal & Regulation               1
           Markets                          1
...                                       ...
2023-04-14 Markets                          1
           Politics                         1
           Stock Commentary                 1
           Stock Movement                   1
           Treasuries & Corporate Debt      1

[23204 rows x 1 columns]

In [172]:
tesla_topics_count = tesla_topics.groupby(["date", "topic"]).size().reset_index(name='topic_count')
tesla_topics_count.topic_count.value_counts()

1    23204
Name: topic_count, dtype: int64

In [159]:
tesla_topics_count = pd.DataFrame(tesla_topics.groupby(["date","topic"])["topic"].count())
tesla_topics_count = tesla_topics_count.rename(columns = {"topic": "topic_count"})
tesla_topics_count = tesla_topics_count.reset_index()
tesla_topics_count = tesla_topics_count.pivot(index = "date", columns = "topic", values = "topic_count")
tesla_topics_count = tesla_topics_count.fillna(0.0)

In [162]:
tesla_topics_count

topic       Analyst Update  Company & Product News  Currencies  Dividend  \
date                                                                       
2017-01-02             1.0                     1.0         0.0       0.0   
2017-01-03             1.0                     1.0         0.0       0.0   
2017-01-04             1.0                     1.0         0.0       0.0   
2017-01-05             1.0                     1.0         0.0       0.0   
2017-01-06             1.0                     1.0         0.0       0.0   
...                    ...                     ...         ...       ...   
2023-04-10             1.0                     1.0         0.0       1.0   
2023-04-11             1.0                     1.0         0.0       0.0   
2023-04-12             0.0                     1.0         0.0       0.0   
2023-04-13             1.0                     1.0         0.0       0.0   
2023-04-14             0.0                     1.0         0.0       0.0   

topic       Earnings  Energy & Oil  Fed & Central Banks  Financials  \
date                                                                  
2017-01-02       0.0           0.0                  0.0         0.0   
2017-01-03       0.0           0.0                  0.0         1.0   
2017-01-04       1.0           1.0                  0.0         1.0   
2017-01-05       0.0           1.0                  1.0         1.0   
2017-01-06       0.0           0.0                  0.0         0.0   
...              ...           ...                  ...         ...   
2023-04-10       1.0           1.0                  0.0         1.0   
2023-04-11       1.0           0.0                  0.0         1.0   
2023-04-12       1.0           0.0                  1.0         1.0   
2023-04-13       0.0           1.0                  0.0         1.0   
2023-04-14       1.0           1.0                  0.0         1.0   

topic       General News & Opinion  Gold, Metals & Materials  IPO  \
date                                                                
2017-01-02                     1.0                       0.0  0.0   
2017-01-03                     1.0                       0.0  0.0   
2017-01-04                     1.0                       0.0  0.0   
2017-01-05                     1.0                       0.0  0.0   
2017-01-06                     1.0                       0.0  0.0   
...                            ...                       ...  ...   
2023-04-10                     1.0                       0.0  0.0   
2023-04-11                     1.0                       0.0  0.0   
2023-04-12                     1.0                       0.0  0.0   
2023-04-13                     1.0                       1.0  0.0   
2023-04-14                     1.0                       0.0  0.0   

topic       Legal & Regulation  M&A & Investments  Macro  Markets  \
date                                                                
2017-01-02                 1.0                0.0    0.0      1.0   
2017-01-03                 1.0                1.0    1.0      0.0   
2017-01-04                 1.0                1.0    1.0      1.0   
2017-01-05                 1.0                0.0    0.0      1.0   
2017-01-06                 1.0                0.0    1.0      1.0   
...                        ...                ...    ...      ...   
2023-04-10                 1.0                1.0    1.0      1.0   
2023-04-11                 1.0                1.0    1.0      1.0   
2023-04-12                 1.0                1.0    1.0      1.0   
2023-04-13                 1.0                0.0    1.0      1.0   
2023-04-14                 1.0                1.0    1.0      1.0   

topic       Personnel Change  Politics  Stock Commentary  Stock Movement  \
date                                                                       
2017-01-02               0.0       0.0               1.0             0.0   
2017-01-03               0.0       0.0               1.0       

In [161]:
# Specify the columns you want to plot
columns_to_plot = list(tesla_topics_count.columns)

# Create the figure
fig = go.Figure()

# Iterate over the columns and add traces to the figure
for column in columns_to_plot:
    fig.add_trace(go.Scatter(x=tesla_topics_count.index, y=tesla_topics_count[column], name=column))

# Update the layout
fig.update_layout(title='Topics Over Time', xaxis_title='Datetime', yaxis_title='Value')

# Display the plot
fig.show()



In [136]:
tesla_topics

date                        topic  Vader_sentim
0      2017-01-02               Analyst Update        2.6299
1      2017-01-02       Company & Product News        5.0529
2      2017-01-02       General News & Opinion       -0.0941
3      2017-01-02           Legal & Regulation       -2.3734
4      2017-01-02                      Markets        0.5106
...           ...                          ...           ...
23199  2023-04-14                      Markets        0.4576
23200  2023-04-14                     Politics        0.0273
23201  2023-04-14             Stock Commentary       23.7870
23202  2023-04-14               Stock Movement       -0.2660
23203  2023-04-14  Treasuries & Corporate Debt       -0.0128

[23204 rows x 3 columns]

In [141]:
tesla_topics_pivot = tesla_topics.pivot(index = "date", columns = "topic",values=["Vader_sentim"])
tesla_topics_pivot = tesla_topics_pivot.ffill()
tesla_topics_pivot = tesla_topics_pivot.fillna(0.0)

In [143]:
tesla_topics_pivot.corr()

Vader_sentim  \
topic                                    Analyst Update   
             topic                                        
Vader_sentim Analyst Update                    1.000000   
             Company & Product News            0.087883   
             Currencies                       -0.001399   
             Dividend                         -0.016891   
             Earnings                          0.098738   
             Energy & Oil                      0.089279   
             Fed & Central Banks              -0.023650   
             Financials                        0.176680   
             General News & Opinion           -0.008364   
             Gold, Metals & Materials          0.006361   
             IPO                               0.016098   
             Legal & Regulation               -0.038319   
             M&A & Investments                -0.003586   
             Macro                             0.024842   
             Markets                           0.126787   
             Personnel Change                 -0.006964   
             Politics                          0.029428   
             Stock Commentary                  0.177981   
             Stock Movement                    0.304633   
             Treasuries & Corporate Debt       0.066775   

                                                                            \
topic                                    Company & Product News Currencies   
             topic                                                           
Vader_sentim Analyst Update                            0.087883  -0.001399   
             Company & Product News                    1.000000  -0.040783   
             Currencies                               -0.040783   1.000000   
             Dividend                                  0.188999  -0.068071   
             Earnings                                  0.253471  -0.054556   
             Energy & Oil                              0.061414   0.028898   
             Fed & Central Banks                       0.018929  -0.015242   
             Financials                                0.159981  -0.012920   
             General News & Opinion                    0.596695  -0.016431   
             Gold, Metals & Materials                  0.026721  -0.021211   
             IPO                                       0.034348   0.009539   
             Legal & Regulation                       -0.237662  -0.005165   
             M&A & Investments                         0.172236  -0.084111   
             Macro                                     0.089980   0.001431   
             Markets                                   0.108353  -0.014337   
             Personnel Change                          0.036979  -0.010279   
             Politics                                  0.115980   0.018990   
             Stock Commentary                          0.623650  -0.032193   
             Stock Movement                            0.353356  -0.011751   
             Treasuries & Corporate Debt               0.036872   0.007154   

                                                                           \
topic                                     Dividend  Earnings Energy & Oil   
             topic                                                          
Vader_sentim Analyst Update              -0.016891  0.098738     0.089279   
             Company & Product News       0.188999  0.253471     0.061414   
             Currencies                  -0.068071 -0.054556     0.028898   
             Dividend                     1.000000  0.189893    -0.004606   
             Earnings                     0.189893  1.000000     0.003973   
             Energy & Oil                -0.004606  0.003973     1.000000   
             Fed & Central Banks          0.019838  0.099417    -0.005701   
             Financials                   0.127785  0.503577     0.014410   
             General News & Opinion       0

In [113]:
fig = px.line(moderna_topics, x='date', y='Vader_sentim', color='topic', labels={'Vader_sentim': 'Sentiment'})

# Update the layout
fig.update_layout(
    title='Topic-Sentiment Pair Analysis',
    xaxis_title='Date',
    yaxis_title='Sentiment per Topic',
    legend_title='Topic'
)
fig.show()

In [125]:
fig = px.line(tesla_topics, x='date', y='Vader_sentim', color='topic', labels={'Vader_sentim': 'Sentiment'})

# Update the layout
fig.update_layout(
    title='Topic-Sentiment Pair Analysis - Tesla',
    xaxis_title='Date',
    yaxis_title='Sentiment per Topic',
    legend_title='Topic'
)
# Show the graph
fig.show()

In [124]:
fig = px.line(apple_topics, x='date', y='Vader_sentim', color='topic', labels={'Vader_sentim': 'Sentiment'})
# Update the layout
fig.update_layout(
    title='Topic-Sentiment Pair Analysis - Apple',
    xaxis_title='Date',
    yaxis_title='Sentiment per Topic',
    legend_title='Topic'
)
# Show the graph
fig.show()

In [ ]:
# Calculate the average tweet length in characters
average_length = twitter_subset_topics_df["text"].apply(len).mean()

# Print the result
print(f"The average tweet length is {average_length:.2f} characters.")


In [54]:
# Count the number of tweets exceeding 512 characters
count_exceeding_280 = sum(twitter_subset_topics_df["text"].apply(len) > 512)
# Count the number of tweets exceeding 800 characters
count_exceeding_800 = sum(twitter_subset_topics_df["text"].apply(len) > 800)
# Print the results
print(f"Number of tweets exceeding 512 characters: {count_exceeding_280}")
print(f"Number of tweets exceeding 800 characters: {count_exceeding_800}")


Number of tweets exceeding 512 characters: 7
Number of tweets exceeding 800 characters: 1


In [61]:
for comp in companies:
    twitter_subset_topics_df = twitter_subset[twitter_subset["company"] == comp]
    twitter_subset_topics_df["topic"] = twitter_subset_topics_df["text"].progress_apply(lambda tweet: handle_topic_classifier(tweet))
    twitter_subset_topics_df["date"] = pd.to_datetime(twitter_subset_topics_df["datetime"].dt.date)
    twitter_subset_topics_df = twitter_subset_topics_df.set_index('date')
    twitter_subset_topics_df = twitter_subset_topics_df.pivot_table(index='date', columns='topic', aggfunc='size', fill_value=0)
    tw_daily = twitter_subset_topics_df.resample('D').size().reset_index(name='tweet_count')
    twitter_subset_topics_df = tw_daily.merge(twitter_subset_topics_df, on='date')
    twitter_subset_topics_df["company"] = comp
    topics_final_df = pd.read_csv(topic_modelling+ "/topic_over_time_companies.csv")
    topics_final_df = pd.concat([topics_final_df, twitter_subset_topics_df])
    topics_final_df = topics_final_df.fillna(0.0)
    topics_final_df.to_csv(topic_modelling+ "/topic_over_time_companies.csv", index = False)
    

progress bar: 100%|██████████| 184195/184195 [1:41:22<00:00, 30.28it/s]


In [73]:
test = pd.DataFrame(columns = list(topics_final_df.columns))

In [59]:
#test.to_csv(topic_modelling+ "/topic_over_time_companies.csv", index = False)

In [63]:
topics_final_df = pd.read_csv(topic_modelling+ "/topic_over_time_companies.csv")
topics_final_df

date  tweet_count  Analyst Update   
0              2017-01-03            1               0  \
1              2017-01-04            1               0   
2              2017-01-05            1               0   
3              2017-01-09            1               0   
4              2017-01-10            1               0   
...                   ...          ...             ...   
6211  2023-04-10 00:00:00            1               2   
6212  2023-04-11 00:00:00            1               0   
6213  2023-04-12 00:00:00            1               1   
6214  2023-04-13 00:00:00            1               0   
6215  2023-04-14 00:00:00            1               0   

      Company & Product News  Earnings  Energy & Oil  Fed & Central Banks   
0                          1         0             0                    0  \
1                          3         0             0                    0   
2                          0         0             0                    0   
3                          8         0             0                    0   
4                          1         0             0                    0   
...                      ...       ...           ...                  ...   
6211                      24         1             0                    0   
6212                      43         0             0                    0   
6213                      10         0             0                    0   
6214                      13         0             0                    0   
6215                       9         0             0                    0   

      General News & Opinion  Legal & Regulation  M&A & Investments  ...   
0                          0                   0                  0  ...  \
1                          0                   0                  0  ...   
2                          0                   0                  0  ...   
3                          0                   0                  0  ...   
4                          0                   0                  0  ...   
...                      ...                 ...                ...  ...   
6211                      13                   0                  0  ...   
6212                       3                   8                  2  ...   
6213                       1                   2                  1  ...   
6214                       4                   8                  0  ...   
6215                       1                   3                  0  ...   

      Stock Commentary  Stock Movement  Financials   
0                    0               1           0  \
1                    3               0           0   
2                    1               0           0   
3                    1               0           0   
4                    1               0           0   
...                ...             ...         ...   
6211                20               2           0   
6212                12               7           0   
6213                 9               0           0   
6214                 9               2           0   
6215                15               2           0   

      Treasuries & Corporate Debt  Dividend  Personnel Change  IPO  company   
0                               0         0                 0    0  moderna  \
1                               0         0                 0    0  moderna   
2                               0         0                 0    0  moderna   
3                               0         0                 0    0  moderna   
4                               0         0                 0    0  moderna   
...                           ...       ...               ...  ...      ...   
6211                            0         0                 0    0   google   
6212                            0         0                 0    0   google   
6213                            1         0                 1    0   google   
6214                            0         0    

In [69]:
twitter_subset_final = topics_final_df[topics_final_df["company"] == "tesla"]
twitter_subset_final = twitter_subset_final.set_index("date")

In [70]:
# twitter_subset_final = twitter_subset_final.iloc[:,:21]

# for col_name in list(twitter_subset_final.columns): 
    
#     twitter_subset_final["r42" + col_name] = twitter_subset_final[col_name].rolling(42, min_periods = 1).mean()

In [71]:


# Specify the columns you want to plot
columns_to_plot = list(twitter_subset_final.columns)

# Create the figure
fig = go.Figure()

# Iterate over the columns and add traces to the figure
for column in columns_to_plot:
    fig.add_trace(go.Scatter(x=twitter_subset_final.index, y=twitter_subset_final[column], name=column))

# Update the layout
fig.update_layout(title='Topics Over Time', xaxis_title='Datetime', yaxis_title='Value')

# Display the plot
fig.show()



---
### Eikon Topics for Moderna

In [81]:
eikon_subset.company.value_counts()
companies = ["apple", "tesla", "moderna"]

In [90]:
eikon_subset

Empty DataFrame
Columns: [date, news_count, tweet_count, Analyst Update, Company & Product News, Currencies, Dividend, Earnings, Energy & Oil, Fed & Central Banks, Financials, General News & Opinion, Gold, Metals & Materials, IPO, Legal & Regulation, M&A & Investments, Macro, Markets, Personnel Change, Politics, Stock Commentary, Stock Movement, Treasuries & Corporate Debt, company]
Index: []

[0 rows x 24 columns]

In [175]:
eikon_subset

datetime  company  \
0     2017-01-02 12:44:28    apple   
1     2017-01-02 16:34:58    apple   
2     2017-01-02 09:24:17    apple   
3     2017-01-02 09:52:42    apple   
4     2017-01-02 22:54:59    tesla   
...                   ...      ...   
44418 2023-04-07 16:24:11    tesla   
44419 2023-04-07 18:23:42    tesla   
44420 2023-04-07 19:02:55    tesla   
44421 2023-04-07 20:17:22  moderna   
44422 2023-04-07 23:12:31    tesla   

                                                    text  \
0      Apple Inc. (AAPL) Sees Large Drop in Short Int...   
1      JLB & Associates Inc. Has $10,751,000 Position...   
2      German and French share indexes start 2017 on ...   
3      BUZZ-Dialog Semi: Falls on report Apple plans ...   
4      Tesla Motors, Inc. (TSLA) Downgraded by Vetr Inc.   
...                                                  ...   
44418  UPDATE 1-Tesla recalls 422 U.S. vehicles over ...   
44419  Used U.S. electric vehicle sales jump as price...   
44420  Tesla just flashed a sell signal that could sp...   
44421  Catalyst Watch: Eyes on inflation data, big ba...   
44422  U.S. opens safety probe into Tesla that struck...   

                                            cleaned_text  
0      apple inc apple sees large drop in short interest  
1      associates inc has $ 10,751,000 position in ap...  
2      german and french share indexes start 2017 on ...  
3      buzz dialog semi falls on report apple plans i...  
4               tesla motors inc tesla downgraded by inc  
...                                                  ...  
44418  update 1 tesla recalls 422 vehicles over suspe...  
44419    used electric vehicle sales jump as prices fall  
44420  tesla just flashed a sell signal that could sp...  
44421  catalyst watch eyes on inflation data big bank...  
44422  opens safety probe into tesla that struck stud...  

[44423 rows x 4 columns]

In [177]:
with tf.device('/device:GPU:0'):
    eikon_df["topic"] = eikon_df["text"].progress_apply(lambda tweet: handle_topic_classifier(tweet))

progress bar: 100%|██████████| 44423/44423 [1:31:15<00:00,  8.11it/s]     


In [178]:
eikon_df

datetime  source           stock  \
0     2017-01-02 12:44:28  ZOLCOM         AAPL.OQ   
1     2017-01-02 16:34:58  ZOLCOM         AAPL.OQ   
2     2017-01-02 09:24:17    RTRS    .GDAXI .IBEX   
3     2017-01-02 09:52:42    RTRS  AAPL.O DLGS.DE   
4     2017-01-02 22:54:59  AMEBAN         TSLA.OQ   
...                   ...     ...             ...   
44418 2023-04-07 16:24:11    RTRS          TSLA.O   
44419 2023-04-07 18:23:42    RTRS     TSLA.O GM.N   
44420 2023-04-07 19:02:55  BUSINT          TSLA.O   
44421 2023-04-07 20:17:22  SEECOM   IMG.TO PSMT.O   
44422 2023-04-07 23:12:31    RTRS          TSLA.O   

                                                    text  company  \
0      Apple Inc. (AAPL) Sees Large Drop in Short Int...    apple   
1      JLB & Associates Inc. Has $10,751,000 Position...    apple   
2      German and French share indexes start 2017 on ...    apple   
3      BUZZ-Dialog Semi: Falls on report Apple plans ...    apple   
4      Tesla Motors, Inc. (TSLA) Downgraded by Vetr Inc.    tesla   
...                                                  ...      ...   
44418  UPDATE 1-Tesla recalls 422 U.S. vehicles over ...    tesla   
44419  Used U.S. electric vehicle sales jump as price...    tesla   
44420  Tesla just flashed a sell signal that could sp...    tesla   
44421  Catalyst Watch: Eyes on inflation data, big ba...  moderna   
44422  U.S. opens safety probe into Tesla that struck...    tesla   

                                            cleaned_text  Finbert_sentim  \
0      apple inc apple sees large drop in short interest            -1.0   
1      associates inc has $ 10,751,000 position in ap...             0.0   
2      german and french share indexes start 2017 on ...            -1.0   
3      buzz dialog semi falls on report apple plans i...            -1.0   
4               tesla motors inc tesla downgraded by inc            -1.0   
...                                                  ...             ...   
44418  update 1 tesla recalls 422 vehicles over suspe...            -1.0   
44419    used electric vehicle sales jump as prices fall            -1.0   
44420  tesla just flashed a sell signal that could sp...             1.0   
44421  catalyst watch eyes on inflation data big bank...             0.0   
44422  opens safety probe into tesla that struck stud...            -1.0   

       Finbert_pos  Finbert_neg  Finbert_neut  Textblob_senti  Textblob_obj  \
0         0.019455     0.965669      0.014876        0.107143      0.364286   
1         0.039715     0.015316      0.944969        0.000000      0.000000   
2         0.015887     0.972655      0.011458        0.000000      0.000000   
3         0.012941     0.917182      0.069877        0.000000      0.000000   
4         0.031287     0.625415      0.343297        0.000000      0.000000   
...            ...          ...           ...             ...           ...   
44418     0.010826     0.962579      0.026595        0.000000      0.000000   
44419     0.028715     0.933346      0.037939        0.000000      0.000000   
44420     0.530141     0.445824      0.024035        0.500000      0.500000   
44421     0.033585     0.044580      0.921835        0.000000      0.100000   
44422     0.039262     0.852507      0.108230        0.000000      0.000000   

       Vader_neg  Vader_neut  Vader_pos  Vader_sentim                   topic  
0          0.174       0.579      0.248        0.2263          Stock Movement  
1          0.000       1.000      0.000        0.0000        Stock Commentary  
2          0.206       0.638      0.156       -0.1779                 Markets  
3          0.189       0.811      0.000       -0.2732  Company & Product News  
4          0.000       1.000      0.000        0.0000          Analyst Update  
...          ...         ...        ...           ...                     ...  
44418      0.000       1.000      0.000        0.0000  Company & Product News  
44419      0.000       1.000      0.000        0.

In [92]:
# eikon_subset["topic"] = eikon_subset["text"].progress_apply(lambda tweet: handle_topic_classifier(tweet))

for comp in companies:
    eikon_subset = eikon_df[eikon_df["company"] == comp]
    eikon_subset["topic"] = eikon_subset["text"].progress_apply(lambda tweet: handle_topic_classifier(tweet))
    eikon_subset["date"] = pd.to_datetime(eikon_subset["datetime"].dt.date)
    eikon_subset = eikon_subset.set_index('date')
    eikon_subset = eikon_subset.pivot_table(index='date', columns='topic', aggfunc='size', fill_value=0)
    tw_daily = eikon_subset.resample('D').size().reset_index(name='news_count')
    eikon_subset = tw_daily.merge(twitter_subset_topics_df, on='date')
    eikon_subset["company"] = comp
    topics_final_df = pd.read_csv(topic_modelling+ "/eikon_topic_over_time_companies.csv")
    topics_final_df = pd.concat([topics_final_df, eikon_subset])
    topics_final_df = topics_final_df.fillna(0.0)
    topics_final_df.to_csv(topic_modelling+ "/eikon_topic_over_time_companies.csv", index = False)

progress bar: 100%|██████████| 6944/6944 [02:34<00:00, 45.05it/s]


In [144]:
topics_final_df = pd.read_csv(topic_modelling+ "/eikon_topic_over_time_companies.csv")
eikon_subset_final = topics_final_df[topics_final_df["company"] == ""]
eikon_subset_final = eikon_subset_final.set_index("date")

In [145]:
columns_to_plot = list(eikon_subset_final.columns)
# Create the figure
fig = go.Figure()
# Iterate over the columns and add traces to the figure
for column in columns_to_plot:
    fig.add_trace(go.Scatter(x=eikon_subset_final.index, y=eikon_subset_final[column], name=column))
# Update the layout
fig.update_layout(title='Topics Count Over Time - Tesla', xaxis_title='Date', yaxis_title='News Count')
# Display the plot
fig.show()

In [ ]:
topics_final_df = pd.read_csv(topic_modelling+ "/twitter_topic_over_time_companies.csv")
eikon_subset_final = topics_final_df[topics_final_df["company"] == ""]
eikon_subset_final = eikon_subset_final.set_index("date")